In [11]:
from ipywidgets import interact, interactive, fixed, interact_manual, FloatSlider
import ipywidgets as widgets
import numpy as np
import math
from ipythonblocks import show_color

In [12]:
def Colour_Name(hue, saturation, brightness):
# paramétrer des contraintes: brightness cannot be 100% if saturation = 100%
# hue name
    hues = {0: 'red',
     15: 'red-orange',
     30: 'orange',
     45: 'orange-yellow',
     60: 'yellow',
     75: 'yellow-chartreuse',
     90: 'chartreuse',
     105: 'chatreuse-green',
     120: 'green',
     135: 'green-jade',
     150: 'jade',
     165: 'jade-cyan',
     180: 'cyan',
     195: 'cyan-azure',
     210: 'azure',
     225: 'azure-blue',
     240: 'blue',
     255: 'blue-violet',
     270: 'violet',
     285: 'violet-magenta',
     300: 'magenta',
     315: 'magenta-rose',
     330: 'rose',
     345: 'rose-red',
     360: 'red'}

    hue_for_dict = min(hues, key=lambda x:abs(x-hue))
    hue_name = hues[hue_for_dict]

    saturation_dict = {0.10: 'grayish', 0.30: 'desaturated', 0.50: 'muted', 0.70: 'saturated', 0.90: 'vivid'}
    saturation_for_dict = min(saturation_dict, key=lambda x:abs(x-saturation))
    saturation_name = saturation_dict[saturation_for_dict]

    brightness_dict = {0.10: 'and very dark', 0.30: 'dark', 0.50: '', 0.70: 'light', 0.90: 'and very light'}
    brightness_for_dict = min(brightness_dict, key=lambda x:abs(x-brightness))
    brightness_name = brightness_dict[brightness_for_dict]

    ColourName = ''
    if saturation == 0:

        if brightness != 0 and brightness !=1:
            #rewrite with brightness instead of whiteness and blackness
            if brightness <= 0.20:
                ColourName = 'very dark gray'
            elif brightness > 0.20 and brightness <= 0.40:
                ColourName = 'dark gray'
            elif brightness > 0.60 and brightness <= 0.80:
                ColourName = 'light gray'
            elif brightness > 0.80 and brightness <= 1.00:
                ColourName = 'very light gray'
            else:
                ColourName = 'medium gray'
        elif brightness == 0:
                ColourName = 'black'
        elif brightness == 1:
                ColourName = 'white'
    else:
        ColourName = "%s %s %s" %(saturation_name, brightness_name, hue_name)
    return ColourName

In [13]:
def rgb2hcb(red, green, blue):
    import numpy as np
    rgb_255 = np.array([red,green,blue])
    rgb_percent = rgb_255 / 255
    diff = np.max(rgb_percent)-np.min(rgb_percent)
    red_pc = rgb_percent[0]
    green_pc = rgb_percent[1]
    blue_pc = rgb_percent[2]

    # calculate hue
    if np.max(rgb_percent) == np.min(rgb_percent):
        hue = 0
    elif np.max(rgb_percent) == red_pc:
        hue = (60 * ((green_pc-blue_pc)/diff) + 360) % 360
    elif np.max(rgb_percent) == green_pc:
        hue = (60 * ((blue_pc-red_pc)/diff) + 120) % 360
    elif np.max(rgb_percent) == blue_pc:
        hue = (60 * ((red_pc-green_pc)/diff) + 240) % 360

    # calculate saturation, whiteness and blackness
    chroma = np.max(rgb_percent) - np.min(rgb_percent)
    whiteness = np.max(rgb_percent) - chroma
    blackness = 1 - chroma - whiteness #reformulate
    total = chroma + blackness + whiteness
    brightness = whiteness + chroma/2 #check if equal to (max(rgb)+min(rgb))/2 and compare against (r+g+b)/3
    
    return show_color(red, green, blue), "Hue: %.2f, Chroma: %.2f, Brightness: %.2f, Whiteness: %.2f Blackness: %.2f, Total: %.2f" % (hue, chroma, brightness, whiteness, blackness, total), Colour_Name(hue, chroma, brightness)

In [14]:
interact(rgb2hcb, red=(0,255,1), green=(0,255,1), blue=(0,255,1))

(None,
 'Hue: 0.00, Chroma: 0.00, Brightness: 0.50, Whiteness: 0.50 Blackness: 0.50, Total: 1.00',
 'medium gray')

<function __main__.rgb2hcb>

In [5]:
def _v(m1, m2, hue):
    hue = hue % 1.0
    if hue < 1/6:
        return m1 + (m2-m1)*hue*6.0
    if hue < 0.5:
        return m2
    if hue < 2/3:
        return m1 + (m2-m1)*(2/3-hue)*6.0
    return m1

def hsl_to_rgb(h, s, l):
    if s == 0.0:
        return int(l*255),int(l*255),int(l*255)
    if l <= 0.5:
        m2 = l * (1.0+s)
    else:
        m2 = l+s-(l*s)
    m1 = 2.0*l - m2
#    return (int(_v(m1, m2, h/360+1/3)*255), int(_v(m1, m2, h/360)*255), int(_v(m1, m2, h/360-1/3)*255)), show_color(int(_v(m1, m2, h/360+1/3)*255), int(_v(m1, m2, h/360)*255), int(_v(m1, m2, h/360-1/3)*255)), Colour_Name(h,s,l)
    return (int(_v(m1, m2, h/360+1/3)*255), int(_v(m1, m2, h/360)*255), int(_v(m1, m2, h/360-1/3)*255))

In [6]:
#from ipywidgets import FloatSlider

sat_widget = FloatSlider(min=0.0, max=1.0, step=0.01)
lum_widget = FloatSlider(min=0.0, max=1.0, step=0.01)

def update_lum_range(*args):
    lum_widget.min = 0.5 * sat_widget.value
    lum_widget.max = 1 - 0.5 * sat_widget.value
sat_widget.observe(update_lum_range, 'value')

In [7]:
def cwb2rgb(h,s,l):
    r,g,b = hsl_to_rgb(h,1,0.5)
    print("RGB values for fully saturated colour:", r,g,b)
    
    r_hsl, g_hsl, b_hsl = hsl_to_rgb(h,s,l)
    print("Hue, Saturation, Lightness conversion: Red: %.2f, Green: %.2f, Blue: %.2f" % (r_hsl, g_hsl, b_hsl))
    w = min(hsl_to_rgb(h,s,l))
    print("Minumum value: %s" %w)
    #spillage problem
    red = min(r*s + w, 255)
    green = min(g*s + w, 255)
    blue = min(b*s + w, 255)
    print("Steve Walesch conversion: Red: %.2f, Green: %.2f, Blue: %.2f" % (red, green, blue))
    return int(red),int(green),int(blue), show_color(int(red), int(green), int(blue)), Colour_Name(h,s,l)

In [8]:
interact(cwb2rgb, h=(0,360,1), s=sat_widget, l=lum_widget); 

RGB values for fully saturated colour: 0 254 255
Hue, Saturation, Lightness conversion: Red: 0.00, Green: 0.00, Blue: 0.00
Minumum value: 0
Steve Walesch conversion: Red: 0.00, Green: 0.00, Blue: 0.00


(0, 0, 0, None, 'black')

In [9]:
interact(rgb2hcb, red=(0,255,1), green=(0,255,1), blue=(0,255,1))

(None,
 'Hue: 0.00, Chroma: 0.00, Brightness: 0.50, Whiteness: 0.50 Blackness: 0.50, Total: 1.00',
 'medium gray')

<function __main__.rgb2hcb>